In [1]:
from qiskit import ClassicalRegister, QuantumRegister, QuantumCircuit,transpile
from qiskit_aer import Aer, AerSimulator
import Our_Qiskit_Functions as oq


import numpy as np
import math as m
S_simulator = Aer.backends('statevector_simulator')[0]
M_simulator = Aer.backends('qasm_simulator')[0]
#get backend not compatible

In [ ]:
#for 32/64 keywords required = 4

# state size= 16
#block size = 32
#keysize = 64
#round = 7 since in each feistal structure there are 4 keywords so 4 round operations hence 28 rounds and 4 rounds added at last
def simon4(qc,state_size):
    if state_size==16:
        rounds=7
        rc=[1,1,1,1,1,0,1,0,0,0,1,0,0,1,0,1,0,1,1,0,0,0,0,1,1,1,0,0,1,1,0,1,1,1,1,1,0,1,0,0,0,1,0,0,1,0,1,0,1,
            1,0,0,0,0,1,1,1,0,0,1,1,0]
    
    #round update function
    #l0->r1->l2->r3->l0
    #r0->l1->r2->l3->r0
    
    for j in range(rounds):
        """reverse indexing -doubt why"""
        for i in range(state_size):
            qc.ccx(l[(i-1)%state_size],l[(i-8)%state_size],r[i])
            qc.cx(l[(i-2)%state_size],r[i])
            qc.cx(k0[i],r[i])

        for i in range (state_size):
            qc.ccx(r[(i-1)%state_size],r[(i-8)%state_size],l[i])
            qc.cx(r[(i-2)%state_size],l[i])
            qc.cx(k1[i],l[i])

        for i in range(state_size):
            qc.ccx(l[(i-1)%state_size],l[(i-8)%state_size],r[i])
            qc.cx(l[(i-2)%state_size],r[i])
            qc.cx(k2[i],r[i])
        
        for i in range (state_size):
            qc.ccx(r[(i-1)%state_size],r[(i-8)%state_size],l[i])
            qc.cx(r[(i-2)%state_size],l[i])
            qc.cx(k3[i],l[i])

        #key expansion
        #reverse indexing
        for i in range(state_size): 
            qc.cx(k1[i],k0[i])
            qc.cx(k1[(i+1)%state_size],k0[i])
            qc.cx(k3[(i+3)%state_size],k0[i])
            qc.cx(k3[(i+4)%state_size],k0[i])
        for i in range(2,state_size):
            qc.x(k0[i])
        if(rc[(j*4)%62]==1):
            qc.x(k0[0])
            
        
        for i in range(state_size): 
            qc.cx(k2[i],k1[i])
            qc.cx(k2[(i+1)%state_size],k1[i])
            qc.cx(k0[(i+3)%state_size],k1[i])
            qc.cx(k0[(i+4)%state_size],k1[i])
        for i in range(2,state_size):
            qc.x(k1[i])
        if(rc[((j*4)+1)%62]==1):
            qc.x(k1[0])
        
        for i in range(state_size): 
            qc.cx(k3[i],k2[i])
            qc.cx(k3[(i+1)%state_size],k2[i])
            qc.cx(k1[(i+3)%state_size],k2[i])
            qc.cx(k1[(i+4)%state_size],k2[i])
        for i in range(2,state_size):
            qc.x(k2[i])
        if(rc[((j*4)+2)%62]==1):
            qc.x(k2[0])
        
        for i in range(state_size): 
            qc.cx(k0[i],k3[i])
            qc.cx(k0[(i+1)%state_size],k3[i])
            qc.cx(k2[(i+3)%state_size],k3[i])
            qc.cx(k2[(i+4)%state_size],k3[i])
        for i in range(2,state_size):
            qc.x(k3[i])
        if(rc[((j*4)+3)%62]==1):
            qc.x(k3[0])
            
    #round complete - remaining 4 real SIMON rounds needed to complete the cipher - very last 4 Feistel rounds must be performed WITHOUT updating the key schedule afterward.
    """why differently"""
    for i in range(state_size):
        qc.ccx(l[(i-1)%state_size],l[(i-8)%state_size],r[i])
        qc.cx(l[(i-2)%state_size],r[i])
        qc.cx(k0[i],r[i])
            
    for i in range(state_size):
        qc.ccx(r[(i-1)%state_size],r[(i-8)%state_size],l[i])
        qc.cx(r[(i-2)%state_size],l[i])
        qc.cx(k1[i],l[i])
            
    for i in range(state_size):
        qc.ccx(l[(i-1)%state_size],l[(i-8)%state_size],r[i])
        qc.cx(l[(i-2)%state_size],r[i])
        qc.cx(k2[i],r[i])
            
    for i in range(state_size):
        qc.ccx(r[(i-1)%state_size],r[(i-8)%state_size],l[i])
        qc.cx(r[(i-2)%state_size],l[i])
        qc.cx(k3[i],l[i])

state_size=16
key_size=64
keywords=int(key_size)/int(state_size)
k0=QuantumRegister(int(state_size),'k0')
k1=QuantumRegister(int(state_size),'k1')
l=QuantumRegister(int(state_size),'l')
r=QuantumRegister(int(state_size),'r')
qc=QuantumCircuit(l,r,k0,k1)

if keywords==4:
    k2=QuantumRegister(int(state_size),'k2')
    k3=QuantumRegister(int(state_size),'k3')
    qc.add_register(k2)
    qc.add_register(k3)
    simon4(qc,int(state_size))

print(qc)

# --- Draw and save the quantum circuit diagram ---
from qiskit.visualization import circuit_drawer
import matplotlib.pyplot as plt

print(f"Circuit created with {qc.num_qubits} qubits and {qc.size()} gates")

try:
    import pylatexenc
    print("\n=== Creating matplotlib figures ===")
    fig = qc.draw(output="mpl", fold=100)  # fold long circuits
    fig.savefig("simon_circuit.svg", format="svg", bbox_inches="tight")
    plt.close(fig)
    print("Saved simon_circuit.svg")
    """fig = qc.draw(output="mpl", fold=100)
    fig.savefig("simon_circuit.png", format="png", dpi=300, bbox_inches="tight")
    plt.close(fig)
    print("Saved simon_circuit.png")"""
except ImportError:
    print("\n=== To create SVG/PNG images, install pylatexenc: ===")
    print("pip install pylatexenc")
    print("Then re-run this script.")





    

        




                                                                             »
  l_0: ───────■──────────────────────────────────■───────────────────────────»
              │                                  │                           »
  l_1: ───────┼────■─────────────────────────────┼────■──────────────────────»
              │    │                             │    │                      »
  l_2: ───────┼────┼────■────────────────────────┼────┼────■─────────────────»
              │    │    │                        │    │    │                 »
  l_3: ───────┼────┼────┼────■───────────────────┼────┼────┼────■────────────»
              │    │    │    │                   │    │    │    │            »
  l_4: ───────┼────┼────┼────┼────■──────────────┼────┼────┼────┼────────────»
              │    │    │    │    │              │    │    │    │            »
  l_5: ───────┼────┼────┼────┼────┼──────────────┼────┼────┼────┼────────────»
              │    │    │    │    │              │  